In [55]:
from sys import path as syspath
from pathlib import Path
import numpy as np

syspath.append(str(Path().home() / "pyref" / "src"))

import pyref as rf
import seaborn as sns
import matplotlib.pyplot as plt
import scienceplots
import matplotlib as mpl
import matplotlib.gridspec as gridspec
from pypxr.structure import *
from pypxr.reflectivity import *
from refnx.dataset import ReflectDataset
from refnx.analysis import Transform, CurveFitter, Objective, GlobalObjective
from refnx._lib.emcee.moves.de import *
from pyref.fitting.logp import LogpExtra_rough


plt.style.use('default')
plt.style.use("science")

sns.set_context("paper", font_scale=1.5)

db = rf.db()

In [40]:
znpc_ocs = db.get_oc("C32H16N8Zn")

en_range = np.linspace(274.9, 295, 1000)

delta_xx = znpc_ocs["xx"].delta(en_range)
delta_zz = znpc_ocs["zz"].delta(en_range)
delta_iso = znpc_ocs["iso"].delta(en_range)

beta_xx = znpc_ocs["xx"].beta(en_range)
beta_zz = znpc_ocs["zz"].beta(en_range)
beta_iso = znpc_ocs["iso"].beta(en_range)

fig = plt.figure(figsize=(12, 12))

<Figure size 1200x1200 with 0 Axes>

In [41]:
znpc_mono = {
    "250": {
        "s": db.get_refl("zrt_250.0_100.csv", "ZnPc"),
        "p": db.get_refl("zrt_250.0_190.csv", "ZnPc"),
        },
    "275": {
        "s": db.get_refl("275.0_100.0_refl.parquet.gzip", "ZnPc"),
        "p": db.get_refl("275.0_190.0_refl.parquet.gzip", "ZnPc"),
        },
    "280": {
        "s": db.get_refl("280.0_100.0_refl.parquet.gzip", "ZnPc"),
        "p": db.get_refl("280.0_190.0_refl.parquet.gzip", "ZnPc"),
        },
    "281": {
        "s": db.get_refl("281.0_100.0_refl.parquet.gzip", "ZnPc"),
        "p": db.get_refl("281.0_190.0_refl.parquet.gzip", "ZnPc"),
        },
    "282": {
        "s": db.get_refl("282.0_100.0_refl.parquet.gzip", "ZnPc"),
        "p": db.get_refl("282.0_190.0_refl.parquet.gzip", "ZnPc"),
        },
    "282.3": {
        "s": db.get_refl("282.3_100.0_refl.parquet.gzip", "ZnPc"),
        "p": db.get_refl("282.3_190.0_refl.parquet.gzip", "ZnPc"),
        },
    "282.7": {
        "s": db.get_refl("282.7_100.0_refl.parquet.gzip", "ZnPc"),
        "p": db.get_refl("282.7_190.0_refl.parquet.gzip", "ZnPc"),
        },
    "283.1": {
        "s": db.get_refl("283.1_100.0_refl.parquet.gzip", "ZnPc"),
        "p": db.get_refl("283.1_190.0_refl.parquet.gzip", "ZnPc"),
        },
    "283.7": {
        "s": db.get_refl("ZnPc_283.7_100.0 (CCD Scan 82865).parquet", "ZnPc"),
        "p": db.get_refl("ZnPc_283.7_190.0 (CCD Scan 82869).parquet", "ZnPc"),
    },
    "284.1": {
        "s": db.get_refl("ZnPc_284.0_100.0 (CCD Scan 82865).parquet", "ZnPc"),
        "p": db.get_refl("ZnPc_284.0_190.0 (CCD Scan 82869).parquet", "ZnPc"),
        },
}

In [88]:
# Load the models
energies = [250, 275, 280, 281, 282, 282.3, 282.7, 283.1, 283.7, 284.1]
models = {}.fromkeys(energies)
oocs = {}.fromkeys(energies)

from pypxr.structure import *
from pypxr.reflectivity import *
from pyref.fitting import from_json
import pickle as pkl
import json

# extract structure params, insturment settings, and optical parameters from each saved json file

for i, en in enumerate(energies):
    if (db.res / f"ZnPc_{en}eV_s_fit.txt").exists():
        s = np.loadtxt(db.res / f"ZnPc_{en}eV_s_fit.txt", delimiter=",").T
    if (db.res / f"ZnPc_{en}eV_p_fit.txt").exists():
        p = np.loadtxt(db.res / f"ZnPc_{en}eV_p_fit.txt", delimiter=",").T
    else:
        pass
    models[en] = {"s": s, "p": p}

    if (db.res / f"ZnPc_{en}eV_ocs.json").exists():
        with open(db.res / f"ZnPc_{en}eV_ocs.json", "r") as f:
            oocs[en] = json.load(f)
    else:
        pass

models = {k: v for k, v in models.items() if v is not None}
# models[250]["s"][:,1]

In [107]:

import matplotlib.transforms as mtransforms

fig, ax = plt.subplot_mosaic(
    [["refl", "delta"],
     ["refl", "beta"]],
     layout = "constrained",
     width_ratios = [1.5, 1],
     figsize = (12, 8),
     dpi = 1000,
)

trans = mtransforms.ScaledTranslation(10/72, -5/72, fig.dpi_scale_trans)

ax["delta"].plot(en_range, delta_xx, label = r"$\delta_{xx}$")
ax["delta"].plot(en_range, delta_zz, label = r"$\delta_{zz}$")
ax["delta"].plot(en_range, delta_iso, label = r"$\delta_{iso}$")

ax["beta"].plot(en_range, beta_xx, label = r"$\beta_{xx}$")
ax["beta"].plot(en_range, beta_zz, label = r"$\beta_{zz}$")
ax["beta"].plot(en_range, beta_iso, label = r"$\beta_{iso}$")

ax["delta"].set(
    ylabel = r"$\delta$ [a.u.]",
    title = "ZnPc Optical Constants",
    xlim = (274.9, 295),
)

ax["delta"].legend(loc = "lower right")
ax["delta"].text(-.165, 1.05, "(b)", transform = ax["delta"].transAxes+trans, fontsize = 16)

ax["beta"].set(
    ylabel = r"$\beta$ [a.u.]",
    xlabel = r"Energy [eV]",
    xlim = (274.9, 295),
)
ax["beta"].sharex(ax["delta"])
ax["beta"].legend()
ax["beta"].text(-.165, 1.05, "(c)", transform = ax["beta"].transAxes+trans, fontsize = 16)
ax["delta"].tick_params(labelbottom = False)


q_range = np.linspace(0.001, 0.3, 1000)

for i, en in enumerate(energies):
    s = znpc_mono[f"{en}"]["s"].iloc[6:]
    p = znpc_mono[f"{en}"]["p"].iloc[6:]


    if en == 250:
        # in p where Refl < 1e-6
        p = p[p["Refl"] > 1e-6]
    # scale data frames to have a 1 order of magnitude offset
    s["Refl"] = 1/10**i * s["Refl"].copy()
    p["Refl"] = 1/10**i * p["Refl"].copy()

    s.plot(x = "Q", y = "Refl", ax = ax["refl"], kind = 'scatter', color = "C0", alpha = 0.5)
    p.plot(x = "Q", y = "Refl", ax = ax["refl"], kind = 'scatter', color = "C2", alpha = 0.5)
    
    if en in [250, 275, 280, 281, 282, 282.3, 282.7, 283.1]:
        q = models[en]["s"][:,0]
        s_model = models[en]["s"][:,1]
        p_model = models[en]["p"][:,1]

        ax["refl"].plot(q, s_model* 1/10**i, color = "k")
        ax["refl"].plot(q, p_model* 1/10**i, color = "k")


ax["refl"].set(
    ylabel = r"$I_r / I_0$",
    xlabel = r"q [$\AA^{-1}$]",
    title = r"ZnPc Reflectivity",
    ylim = (1e-16,1),
    xlim = (0.01, 0.254),
    yscale = "log",
)

ax["refl"].legend(labels = ["s-pol", "p-pol", "Fit"])
ax["refl"].text(-.165, 1.01, "(a)", transform = ax["refl"].transAxes+trans, fontsize = 16)

C:\Users\Harlan Heilman\AppData\Local\Temp\ipykernel_22196\1757745431.py:53: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  s["Refl"] = 1/10**i * s["Refl"].copy()
C:\Users\Harlan Heilman\AppData\Local\Temp\ipykernel_22196\1757745431.py:53: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  s["Refl"] = 1/10**i * s["Refl"].copy()
C:\Users\Harlan Heilman\AppData\Local\Temp\ipykernel_22196\1757745431.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_

Text(-0.165, 1.01, '(a)')